In [1]:
import pandas as pd
import numpy as np

In [2]:
play_df = pd.read_csv("data/plays.csv") # this is loaded with pandas cause its not big and dask has troubles with shifted data in csv

In [3]:
play_df.shape

(19239, 27)

In [4]:
games_df = pd.read_csv("data/games.csv")

In [5]:
one_week_tracking_df = pd.read_csv('data/week1.csv')

In [6]:
one_week_tracking_df.shape

(986022, 19)

In [7]:
week1_games = games_df[games_df.week == 1]
week1_games.shape

(13, 6)

In [8]:
games_n_plays_df = play_df.merge(week1_games, how='inner', on='gameId')
games_n_plays_df.shape

(1034, 32)

In [9]:
group_t = one_week_tracking_df.groupby(['time', 'frameId'])

### Merge all 15 (or different count) features of one timestamp -> player positions and ball position

In [10]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

### Drop all records that doesnt have football

In [11]:
drop_t = group_t.filter(lambda row: (row['displayName'] == 'Football').any())

In [12]:
drop_t.shape

(985286, 19)

In [13]:
one_week_tracking_df.shape

(986022, 19)

In [14]:
print(one_week_tracking_df.shape[0] - drop_t.shape[0])

736


### Drop all values that have only football 

In [15]:
drop_f = drop_t.groupby(['time', 'frameId']).filter(lambda row: (row['displayName'] != 'Football').any()) 

In [16]:
drop_f.shape

(985228, 19)

## Change

In [17]:
print(drop_t.shape[0] - drop_f.shape[0])

58


In [18]:
keep_f = drop_f.copy()

In [19]:
frame2time = keep_f.groupby(['gameId', 'time', 'frameId'])

In [20]:
frame2time.size().sort_index()

gameId      time                      frameId
2018090600  2018-09-07T01:07:14.599Z  1          14
            2018-09-07T01:07:14.700Z  2          14
            2018-09-07T01:07:14.799Z  3          14
            2018-09-07T01:07:14.900Z  4          14
            2018-09-07T01:07:15.000Z  5          14
            2018-09-07T01:07:15.099Z  6          14
            2018-09-07T01:07:15.200Z  7          14
            2018-09-07T01:07:15.299Z  8          14
            2018-09-07T01:07:15.400Z  9          14
            2018-09-07T01:07:15.500Z  10         14
            2018-09-07T01:07:15.599Z  11         14
            2018-09-07T01:07:15.700Z  12         14
            2018-09-07T01:07:15.799Z  13         14
            2018-09-07T01:07:15.900Z  14         14
            2018-09-07T01:07:16.000Z  15         14
            2018-09-07T01:07:16.099Z  16         14
            2018-09-07T01:07:16.200Z  17         14
            2018-09-07T01:07:16.299Z  18         14
            2018-0

In [21]:
prevFrameId = 0
prevPlayId = 0
coef = 1
prevTimestamp = pd.Timestamp('2018-01-01T00:00:00.000Z')
timestampDelta = pd.Timedelta(np.timedelta64(10, 'ms'))

for name, group in frame2time:
    gameId, timestamp, frameId = name
    timestamp = pd.Timestamp(timestamp)

    if frameId >= prevFrameId and timestamp == prevTimestamp:
        prevFrameId = frameId
        newTimestamp = timestamp + (timestampDelta * coef)
        coef += 1
        keep_f['time'].mask(
            (keep_f['gameId'] == gameId) & 
            (keep_f['time'] == timestamp.strftime('%Y-%m-%dT%H:%M:%S.%f')[:-3] + 'Z') &
            (keep_f['frameId'] == frameId), 
            newTimestamp.strftime('%Y-%m-%dT%H:%M:%S.%f')[:-3] + 'Z', 
            inplace=True
        ) 
    else:
        # new play
        coef = 1
        prevFrameId = frameId
        prevTimestamp = timestamp

## Success finally!

In [22]:
type(keep_f)

pandas.core.frame.DataFrame

In [23]:
keep_f.shape

(985228, 19)

### <s>  Drop all timestamps (groups) that have duplicate frame Ids </s>
### Change timestamp for duplicate frame Ids cause they are not duplicate but from different game

In [24]:
def preprocess_df_columns(dataframe: pd.DataFrame) -> pd.Series:
    occurance_list = dataframe.sort_values(['gameId', 'time', 'frameId']).groupby(['gameId', 'time', 'frameId', 'team']).team.cumcount().add(1)
    labels_list = dataframe.sort_values(['gameId', 'time', 'frameId']).groupby(['gameId', 'time', 'frameId']).team.apply(list)
    flat_list = np.array([item for sublist in labels_list for item in sublist])
    merge_list = np.column_stack((occurance_list, flat_list))
    col_list = [f'{row[1]}_{row[0]}' for row in merge_list]
    return pd.Series(col_list)

###  Success now apply to whole week 1
#### First normalize

In [25]:
normalize_tracking = keep_f.copy()

In [26]:
# normalize coordinates
def normalize_x(row):
    if row.playDirection == 'left':
        return 120 - row.x
    return row.x

def normalize_y(row):
    if row.playDirection == 'left':
        return 160/3 - row.y
    return row.y

normalize_tracking.x = normalize_tracking.apply(lambda row: normalize_x(row), axis=1)
normalize_tracking.y = normalize_tracking.apply(lambda row: normalize_y(row), axis=1)

In [27]:
normalize_tracking.shape

(985228, 19)

In [28]:
games_n_plays_df_cleaned = games_n_plays_df.drop(columns=[
    'playDescription', 
    'penaltyJerseyNumbers', 'penaltyCodes', 'gameDate',
])

In [29]:
games_n_plays_df_cleaned.columns

Index(['gameId', 'playId', 'quarter', 'down', 'yardsToGo', 'possessionTeam',
       'playType', 'yardlineSide', 'yardlineNumber', 'offenseFormation',
       'personnelO', 'defendersInTheBox', 'numberOfPassRushers', 'personnelD',
       'typeDropback', 'preSnapVisitorScore', 'preSnapHomeScore', 'gameClock',
       'absoluteYardlineNumber', 'passResult', 'offensePlayResult',
       'playResult', 'epa', 'isDefensivePI', 'gameTimeEastern', 'homeTeamAbbr',
       'visitorTeamAbbr', 'week'],
      dtype='object')

In [30]:
def home_has_possession(row):
    if (row.possessionTeam == row.homeTeamAbbr):
        return 1
    return 0
              
games_n_plays_df_cleaned['homeHasPossesion'] = games_n_plays_df_cleaned.apply(lambda row: home_has_possession(row), axis=1)
games_n_plays_df_cleaned.head(5)

gameId  playId  quarter  down  yardsToGo possessionTeam  \
0  2018090600      75        1     1         15            ATL   
1  2018090600     146        1     1         10            ATL   
2  2018090600     168        1     2         10            ATL   
3  2018090600     190        1     3         10            ATL   
4  2018090600     256        1     3          1            ATL   

         playType yardlineSide  yardlineNumber offenseFormation  \
0  play_type_pass          ATL              20           I_FORM   
1  play_type_pass          PHI              39       SINGLEBACK   
2  play_type_pass          PHI              39          SHOTGUN   
3  play_type_pass          PHI              39          SHOTGUN   
4  play_type_pass          PHI               1          SHOTGUN   

         personnelO  defendersInTheBox  numberOfPassRushers        personnelD  \
0  2 RB, 1 TE, 2 WR                7.0                  4.0  4 DL, 2 LB, 5 DB   
1  1 RB, 1 TE, 3 WR                7.0                  4.0  4 DL, 2 LB, 5 DB   
2  2 RB, 1 TE, 2 WR                6.0                  4.0  4 DL, 2 LB, 5 DB   
3  1 RB, 1 TE, 3 WR                6.0                  5.0  4 DL, 1 LB, 6 DB   
4  2 RB, 3 TE, 0 WR                8.0                  6.0  6 DL, 3 LB, 2 DB   

            typeDropback  preSnapVisitorScore  preSnapHomeScore gameClock  \
0            TRADITIONAL                  0.0               0.0  15:00:00   
1            TRADITIONAL                  0.0               0.0  13:10:00   
2            TRADITIONAL                  0.0               0.0  13:05:00   
3  SCRAMBLE_ROLLOUT_LEFT                  0.0               0.0  13:01:00   
4            TRADITIONAL                  0.0               0.0  10:59:00   

   absoluteYardlineNumber passResult  offensePlayResult  playResult       epa  \
0                    90.0          C                 10          10  0.261827   
1                    49.0          I                  0           0 -0.372360   
2                    49.0          I                  0           0 -0.702779   
3                    49.0          C                 33          33  3.047530   
4                    11.0          I                  0           0 -0.842272   

   isDefensivePI gameTimeEastern homeTeamAbbr visitorTeamAbbr  week  \
0          False        20:20:00          PHI             ATL     1   
1          False        20:20:00          PHI             ATL     1   
2          False        20:20:00          PHI             ATL     1   
3          False        20:20:00          PHI             ATL     1   
4          False        20:20:00          PHI             ATL     1   

   homeHasPossesion  
0                 0  
1                 0  
2                 0  
3                 0  
4                 0

In [31]:
gnp_core_cols = games_n_plays_df_cleaned[
    [
        'gameId', 'playId', 'homeHasPossesion', 
        'isDefensivePI'
    ]
]
gnp_core_cols.columns

Index(['gameId', 'playId', 'homeHasPossesion', 'isDefensivePI'], dtype='object')

In [58]:
def preprocess_df_columns(dataframe: pd.DataFrame) -> pd.Series:
    occurance_list = dataframe.sort_values(['gameId', 'time', 'frameId']).groupby(['gameId', 'time', 'frameId', 'team']).team.cumcount().add(1)
    labels_list = dataframe.sort_values(['gameId', 'time', 'frameId']).groupby(['gameId', 'time', 'frameId']).team.apply(list)
    flat_list = np.array([item for sublist in labels_list for item in sublist])
    merge_list = np.column_stack((occurance_list, flat_list))
    col_list = [f'{row[1]}_{row[0]}' for row in merge_list]
    return pd.Series(col_list)

In [83]:
convert2cols = pd.pivot_table(
    normalize_tracking, 
    index=['time', 'playId', 'gameId'], 
    columns=preprocess_df_columns(normalize_tracking2), values=['x', 'y', 's', 'a', 'dis', 'o'], 
    aggfunc='sum'
)

In [84]:
convert2cols.columns = convert2cols.columns.map('{0[0]}_{0[1]}'.format)

In [85]:
convert2cols.columns

Index(['a_away_1', 'a_away_10', 'a_away_2', 'a_away_3', 'a_away_4', 'a_away_5',
       'a_away_6', 'a_away_7', 'a_away_8', 'a_away_9',
       ...
       'y_home_10', 'y_home_11', 'y_home_2', 'y_home_3', 'y_home_4',
       'y_home_5', 'y_home_6', 'y_home_7', 'y_home_8', 'y_home_9'],
      dtype='object', length=132)

In [86]:
def expand_cols_if_needed(df: pd.DataFrame, column_names = ['x', 'y', 's', 'a', 'dis', 'o']):
    for index in range(1, 12):
        for team in ['home', 'away']:
            for label in column_names:
                col_name = f'{label}_{team}_{index}'
                if col_name not in df:
                    print(f'Expanding {col_name}')
                    df[col_name] = np.nan

In [87]:
expand_cols_if_needed(convert2cols)

Expanding x_away_11
Expanding y_away_11
Expanding s_away_11
Expanding a_away_11
Expanding dis_away_11
Expanding o_away_11


In [88]:
convert2cols.shape

(66803, 138)

In [95]:
sort_index = convert2cols.sort_index(axis=1)
sort_index.columns

Index(['a_away_1', 'a_away_10', 'a_away_11', 'a_away_2', 'a_away_3',
       'a_away_4', 'a_away_5', 'a_away_6', 'a_away_7', 'a_away_8',
       ...
       'y_home_10', 'y_home_11', 'y_home_2', 'y_home_3', 'y_home_4',
       'y_home_5', 'y_home_6', 'y_home_7', 'y_home_8', 'y_home_9'],
      dtype='object', length=138)

In [96]:
rm_index = sort_index.reset_index()
rm_index.head()

time  playId      gameId  a_away_1  a_away_10  \
0  2018-09-07T01:07:14.599Z      75  2018090600      0.01        NaN   
1  2018-09-07T01:07:14.700Z      75  2018090600      0.00        NaN   
2  2018-09-07T01:07:14.799Z      75  2018090600      0.00        NaN   
3  2018-09-07T01:07:14.900Z      75  2018090600      0.00        NaN   
4  2018-09-07T01:07:15.000Z      75  2018090600      0.00        NaN   

   a_away_11  a_away_2  a_away_3  a_away_4  a_away_5  a_away_6  a_away_7  \
0        NaN      0.03       0.0      0.01      0.02      0.01       NaN   
1        NaN      0.03       0.0      0.01      0.02      0.01       NaN   
2        NaN      0.03       0.0      0.01      0.01      0.01       NaN   
3        NaN      0.02       0.0      0.01      0.01      0.01       NaN   
4        NaN      0.02       0.0      0.01      0.01      0.01       NaN   

   a_away_8  a_away_9  a_football_1  a_home_1  a_home_10  a_home_11  a_home_2  \
0       NaN       NaN           0.0      0.01        NaN        NaN      0.42   
1       NaN       NaN           0.0      0.01        NaN        NaN      0.58   
2       NaN       NaN           0.0      0.01        NaN        NaN      0.57   
3       NaN       NaN           0.0      0.01        NaN        NaN      0.48   
4       NaN       NaN           0.0      0.01        NaN        NaN      0.26   

   a_home_3  a_home_4  a_home_5  a_home_6  a_home_7  a_home_8  a_home_9  \
0      0.02      0.03      0.07      0.05      0.04       NaN       NaN   
1      0.02      0.03      0.05      0.07      0.03       NaN       NaN   
2      0.02      0.02      0.03      0.07      0.03       NaN       NaN   
3      0.03      0.03      0.02      0.08      0.03       NaN       NaN   
4      0.02      0.04      0.02      0.07      0.03       NaN       NaN   

   dis_away_1  dis_away_10  dis_away_11  dis_away_2  dis_away_3  dis_away_4  \
0        0.02          NaN          NaN        0.01         0.0         0.0   
1        0.00          NaN          NaN        0.02         0.0         0.0   
2        0.00          NaN          NaN        0.01         0.0         0.0   
3        0.01          NaN          NaN        0.00         0.0         0.0   
4        0.01          NaN          NaN        0.01         0.0         0.0   

   dis_away_5  dis_away_6  dis_away_7  dis_away_8  dis_away_9  dis_football_1  \
0        0.01        0.01         NaN         NaN         NaN             0.0   
1        0.01        0.01         NaN         NaN         NaN             0.0   
2        0.00        0.00         NaN         NaN         NaN             0.0   
3        0.01        0.00         NaN         NaN         NaN             0.0   
4        0.00        0.00         NaN         NaN         NaN             0.0   

   dis_home_1  dis_home_10  dis_home_11  dis_home_2  dis_home_3  dis_home_4  \
0        0.01          NaN          NaN        0.01        0.01        0.04   
1        0.00          NaN          NaN        0.01        0.01        0.00   
2        0.01          NaN          NaN        0.01        0.01        0.02   
3        0.01          NaN          NaN        0.01        0.01        0.03   
4        0.01          NaN          NaN        0.01        0.00        0.01   

   dis_home_5  dis_home_6  dis_home_7  dis_home_8  dis_home_9  o_away_1  \
0        0.01        0.01        0.02         NaN         NaN    289.57   
1        0.01        0.01        0.02         NaN         NaN    289.57   
2        0.00        0.01        0.03         NaN         NaN    288.91   
3        0.01        0.01        0.01         NaN         NaN    288.91   
4        0.01        0.01        0.01         NaN         NaN    288.28   

   o_away_10  o_away_11  o_away_2  o_away_3  o_away_4  o_away_5  o_away_6  \
0        NaN        NaN    290.45    257.61    265.88    250.34    250.10   
1        NaN        NaN    290.45    257.61    265.88    251.59    248.81   
2        NaN        NaN    290.45    257.61    264.92    251.59    248.81   

In [79]:
rm_index.shape

(66803, 141)

In [52]:
gnp_core_cols.columns

Index(['gameId', 'playId', 'homeHasPossesion', 'isDefensivePI'], dtype='object')

In [89]:
merge_week1_plays_games = rm_index.merge(gnp_core_cols, how='left', on=['gameId', 'playId'])
merge_week1_plays_games.head()

time  playId      gameId  a_away_1  a_away_10  a_away_2  a_away_3  a_away_4  a_away_5  a_away_6  a_away_7  a_away_8  a_away_9  a_football_1  a_home_1  a_home_10  a_home_11  a_home_2  a_home_3  a_home_4  a_home_5  a_home_6  a_home_7  a_home_8  a_home_9  dis_away_1  dis_away_10  dis_away_2  dis_away_3  dis_away_4  dis_away_5  dis_away_6  dis_away_7  dis_away_8  dis_away_9  dis_football_1  dis_home_1  dis_home_10  dis_home_11  dis_home_2  dis_home_3  dis_home_4  dis_home_5  dis_home_6  dis_home_7  dis_home_8  dis_home_9  o_away_1  o_away_10  o_away_2  o_away_3  o_away_4  o_away_5  o_away_6  o_away_7  o_away_8  o_away_9  o_football_1  o_home_1  o_home_10  o_home_11  o_home_2  o_home_3  o_home_4  o_home_5  o_home_6  o_home_7  o_home_8  o_home_9  s_away_1  s_away_10  s_away_2  s_away_3  s_away_4  s_away_5  s_away_6  s_away_7  s_away_8  s_away_9  s_football_1  s_home_1  s_home_10  s_home_11  s_home_2  s_home_3  s_home_4  s_home_5  s_home_6  s_home_7  s_home_8  \
0  2018-09-07T01:07:14.599Z      75  2018090600      0.01        NaN      0.03       0.0      0.01      0.02      0.01       NaN       NaN       NaN           0.0      0.01        NaN        NaN      0.42      0.02      0.03      0.07      0.05      0.04       NaN       NaN        0.02          NaN        0.01         0.0         0.0        0.01        0.01         NaN         NaN         NaN             0.0        0.01          NaN          NaN        0.01        0.01        0.04        0.01        0.01        0.02         NaN         NaN    289.57        NaN    290.45    257.61    265.88    250.34    250.10       NaN       NaN       NaN           0.0    105.63        NaN        NaN     70.12    103.05     95.90     81.14    108.23     87.69       NaN       NaN       0.0        NaN      0.02       0.0      0.01      0.01      0.01       NaN       NaN       NaN           0.0      0.01        NaN        NaN      0.09      0.03      0.09      0.03      0.14      0.03       NaN   
1  2018-09-07T01:07:14.700Z      75  2018090600      0.00        NaN      0.03       0.0      0.01      0.02      0.01       NaN       NaN       NaN           0.0      0.01        NaN        NaN      0.58      0.02      0.03      0.05      0.07      0.03       NaN       NaN        0.00          NaN        0.02         0.0         0.0        0.01        0.01         NaN         NaN         NaN             0.0        0.00          NaN          NaN        0.01        0.01        0.00        0.01        0.01        0.02         NaN         NaN    289.57        NaN    290.45    257.61    265.88    251.59    248.81       NaN       NaN       NaN           0.0    105.63        NaN        NaN     70.88    104.57    101.10     82.24    107.33     87.69       NaN       NaN       0.0        NaN      0.03       0.0      0.01      0.01      0.01       NaN       NaN       NaN           0.0      0.01        NaN        NaN      0.10      0.03      0.07      0.04      0.14      0.03       NaN   
2  2018-09-07T01:07:14.799Z      75  2018090600      0.00        NaN      0.03       0.0      0.01      0.01      0.01       NaN       NaN       NaN           0.0      0.01        NaN        NaN      0.57      0.02      0.02      0.03      0.07      0.03       NaN       NaN        0.00          NaN        0.01         0.0         0.0        0.00        0.00         NaN         NaN         NaN             0.0        0.01          NaN          NaN        0.01        0.01        0.02        0.00        0.01        0.03         NaN         NaN    288.91        NaN    290.45    257.61    264.92    251.59    248.81       NaN       NaN       NaN           0.0    107.02        NaN        NaN     71.88    104.57    103.45     83.64    105.87     88.58       NaN       NaN       0.0        NaN      0.02       0.0      0.01      0.01      0.01       NaN       NaN       NaN           0.0      0.01        NaN        NaN      0.13      0.03      0.05      0.04      0.13      0.03       NaN   
3  2018-09-07T01:07:14.900Z      75  2018090600    

In [90]:
merge_week1_plays_games.shape

(66803, 137)

In [91]:
merge_week1_plays_games.isDefensivePI.value_counts()

False    65812
True       991
Name: isDefensivePI, dtype: int64

In [117]:
def convert_df_to_numpy_array(df: pd.DataFrame, groupbyId: list, skipLastListWrapper=False) -> np.array:
    group = df.groupby(groupbyId).cumcount()
    
    if skipLastListWrapper:
        return (
            df.set_index([*groupbyId, group])
               .unstack(fill_value=None)
               .stack().groupby(level=0).agg({'time': 'first', 'isDefensivePI': 'first'})
               .apply(lambda x: x.values.tolist())
               .values.tolist()
        )
    
    return (
        df.set_index([*groupbyId, group])
           .unstack(fill_value=None)
           .stack().groupby(level=0)
           .apply(lambda x: x.values.tolist())
           .values.tolist()
    )

In [123]:
df_labels = merge_week1_plays_games[['gameId', 'playId', 'time', 'isDefensivePI']]

In [93]:
df_features = merge_week1_plays_games.loc[:, merge_week1_plays_games.columns != 'isDefensivePI']

In [110]:
df_features.shape

(66803, 136)

In [139]:
features_list = convert_df_to_numpy_array(df_features, ['playId', 'gameId'])

In [140]:
labels_list = convert_df_to_numpy_array(df_labels, ['playId', 'gameId'], skipLastListWrapper=True)

In [144]:
np.shape(labels_list)

(927, 2)

In [145]:
from operator import itemgetter
import numpy as np

def sort_list_by_col_index(listToSort: np.array, columnIndex: int, deepSort=True) -> np.array:
    if deepSort:
        for i, play in enumerate(listToSort):
            listToSort[i] = sorted(play, key=itemgetter(columnIndex))
        return listToSort
    return sorted(listToSort, key=itemgetter(columnIndex))


def remove_col_from_inner_list(inputList: np.array, columnIndex: int) -> np.array:
    for i, play in enumerate(inputList):
        inputList[i] = np.delete(inputList[i], columnIndex, axis=1)
    return inputList
    
    
def promote_list_item(inputList: np.array, elementToKeepIndex: int) -> np.array:
    """
    Keep only one element from the list and remove list wrapper. 
    Usefull when using list of lists
    """
     # remove list wrapper and col (keep only label)
    new_list = []
    for i, row in enumerate(inputList):
        new_list.append(inputList[i][elementToKeepIndex])
    return new_list

In [146]:
features_sorted = sort_list_by_col_index(features_list, 0)
# when it is sorted remove timestamp from array
features_final = remove_col_from_inner_list(features_sorted, 0)

In [147]:
labels_sorted = sort_list_by_col_index(labels_list, 0, deepSort=False)
# when it is sorted remove timestamp from array
labels_final = promote_list_item(labels_sorted, 1)

In [148]:
np.shape(features_sorted)

(927,)

In [149]:
import os

In [150]:
np.save(os.path.join('data', 'interim', f'features_new_processing.npy'), np.array(features_final))
np.save(os.path.join('data', 'interim', f'labels_new_processing.npy'), np.array(labels_final))

<ipython-input-150-8f090d784fb2>:1: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  np.save(os.path.join('data', 'interim', f'features_new_processing.npy'), np.array(features_final))
